![sqldw_icon.png](https://github.com/microsoft/sql-data-warehouse-samples/raw/master/samples/sqlops/MonitoringScripts/sqldw_icon.png)
## Azure SQL DW Insights
https://github.com/Microsoft/sql-data-warehouse-samples/tree/master/samples/sqlops/MonitoringScripts

#### Documentation
##### [Data_Skew](https://docs.microsoft.com/en-us/azure/sql-data-warehouse/sql-data-warehouse-tables-distribute#troubleshooting-data-skew), [Low_Rowgroup_Quality](https://docs.microsoft.com/en-us/azure/sql-data-warehouse/sql-data-warehouse-memory-optimizations-for-columnstore-compression#how-to-monitor-rowgroup-quality), [Table_Statistics](https://docs.microsoft.com/en-us/azure/sql-data-warehouse/sql-data-warehouse-tables-statistics#updating-statistics), [Github](https://github.com/Microsoft/sql-data-warehouse-samples)

## Impacted Tables

In [3]:
-- data skew -> cmp_rows>1mil, skew >= 10%
-- missing stats -> cmp_rows>1mil, ctl_rows=1000
-- outdated stats -> cmp_rows>1mil, cmp_rows <> ctl_rows (for (cmp_rows-ctl_rows) > 20%)

declare @minRows int=1000000;
declare @minSkewPercent decimal=10.0;
declare @missingStatCtlRowCount int=1000;
declare @CtlCmpRowDifferencePercentageForOutdatedStats decimal=20.0;

with cmp_details as
(
       select tm.object_id, ps.index_id, ps.distribution_id, count(ps.partition_number) [partitions], sum(ps.row_count) cmp_row_count
       from sys.dm_pdw_nodes_db_partition_stats ps
              join sys.pdw_nodes_tables nt on nt.object_id=ps.object_id and ps.distribution_id=nt.distribution_id
              join sys.pdw_table_mappings tm on tm.physical_name=nt.name
       where ps.index_id<2
       group by tm.object_id, ps.index_id, ps.distribution_id
)
, cmp_summary as
(
       select object_id, index_id, sum(cmp_row_count) cmp_row_count
              , (max(cmp_row_count)-min(cmp_row_count)) highest_skew_rows_difference
              , convert(decimal(10,2),((max(cmp_row_count) - min(cmp_row_count))*100.0 / nullif(sum(cmp_row_count),0))) skew_percent
       from cmp_details
       group by object_id, index_id
)
, ctl_summary as
(
       select t.object_id, i.index_id, s.name sch_name, t.name table_name, i.type_desc table_type, dp.distribution_policy_desc distribution_type, count(p.partition_number) [partitions], sum(p.rows) ctl_row_count
       from sys.schemas s
              join sys.tables t on t.schema_id=s.schema_id
              join sys.pdw_table_distribution_properties dp on dp.object_id=t.object_id
              join sys.indexes i on i.object_id=t.object_id and i.index_id<2
              join sys.partitions p on p.object_id=t.object_id and p.index_id=i.index_id
       group by t.object_id, i.index_id, s.name, t.name, i.type_desc, dp.distribution_policy_desc
)
, [all_results] as
(
       select ctl.object_id, ctl.index_id, ctl.sch_name, ctl.table_name, ctl.table_type, ctl.distribution_type, ctl.[partitions]
              , ctl.ctl_row_count, cmp.cmp_row_count, convert(decimal(10,2),(abs(ctl.ctl_row_count - cmp.cmp_row_count)*100.0 / nullif(cmp.cmp_row_count,0))) ctl_cmp_difference_percent
              , cmp.highest_skew_rows_difference, cmp.skew_percent
              , case 
                     when (ctl.ctl_row_count = @missingStatCtlRowCount) then 'missing stats'
                     when ((ctl.ctl_row_count <> cmp.cmp_row_count) and ((abs(ctl.ctl_row_count - cmp.cmp_row_count)*100.0 / nullif(cmp.cmp_row_count,0)) > @CtlCmpRowDifferencePercentageForOutdatedStats)) then 'outdated stats'
                     else null
                end stat_info
              , case when (cmp.skew_percent >= @minSkewPercent) then 'data skew' else null end skew_info
       from ctl_summary ctl
              join cmp_summary cmp on ctl.object_id=cmp.object_id and ctl.index_id=cmp.index_id
)
select *
from [all_results]
where cmp_row_count>@minRows and (stat_info is not null or skew_info is not null)
order by sch_name, table_name

(15 rows affected)

Total execution time: 00:00:07.506

object_id index_id sch_name table_name table_type distribution_type partitions ctl_row_count cmp_row_count ctl_cmp_difference_percent highest_skew_rows_difference skew_percent stat_info skew_info 1109631046 1 dbo Claim11 CLUSTERED COLUMNSTORE HASH 1 1000 30697250 100.00 4293 0.01 missing stats NULL 1429632186 1 dbo Claim12 CLUSTERED COLUMNSTORE HASH 1 61394506 61394506 0.00 30700607 50.01 NULL data skew 157295670 1 dbo ctiiSuperTableSum CLUSTERED COLUMNSTORE HASH 1 1000 2608713636 100.00 29431 0.00 missing stats NULL 284580102 1 dbo hashOrganicRAMP CLUSTERED COLUMNSTORE HASH 1 1000 113220791 100.00 27560 0.02 missing stats NULL 1719781284 1 dbo Inforce12 CLUSTERED COLUMNSTORE HASH 1 1027364723 1027364723 0.00 342466049 33.33 NULL data skew 1445632243 1 dbo Inforce12xxx CLUSTERED COLUMNSTORE HASH 1 1027364723 1027364723 0.00 342466049 33.33 NULL data skew 1189631331 1 dbo Input11 CLUSTERED COLUMNSTORE HASH 1 1000 135579460 100.00 8063 0.01 missing stats NULL 1181963287 1 dbo MI_2019Assumption CLUSTERED COLUMNSTORE ROUND_ROBIN 1 1000 13866640 99.99 12550 0.09 missing stats NULL 87775470 1 dbo Output12 CLUSTERED COLUMNSTORE HASH 1 14401258581 23160799911 37.82 4532141 0.02 outdated stats NULL 991394651 1 dbo output12_A CLUSTERED COLUMNSTORE ROUND_ROBIN 1 400 14371388 100.00 835 0.01 outdated stats NULL 1614680850 1 dbo Output12xxx CLUSTERED COLUMNSTORE HASH 1 9515855835 14401258581 33.92 3693848 0.03 outdated stats NULL 1173631274 1 dbo Premium11 CLUSTERED COLUMNSTORE HASH 1 1000 158515622 100.00 9279 0.01 missing stats NULL 1461632300 1 dbo Premium12 CLUSTERED COLUMNSTORE HASH 1 317031244 317031244 0.00 158521552 50.00 NULL data skew 612249286 1 dbo RamTestHash CLUSTERED COLUMNSTORE HASH 1 1000 50329620 100.00 150516 0.30 missing stats NULL 1102679026 1 dbo TempDeleteMe4 CLUSTERED COLUMNSTORE HASH 1 1000 4070752305 100.00 1606222 0.04 missing stats NULL

## Latest Backup

In [4]:
/* Latest backup deatils */
SELECT TOP 1
	start_time									[start_time]
	, end_time									[end_time]
	, progress									[progress_percent]
	, DATEDIFF(SECOND, start_time, end_time)	[duration_seconds]
FROM
	[sys].[pdw_loader_backup_runs]
ORDER BY
	[run_id] DESC;

(1 row affected)

Total execution time: 00:00:00.180

start_time end_time progress_percent duration_seconds 2019-10-01 13:16:38.093 2019-10-01 13:16:55.937 100 17

## Memory Consumption

In [5]:
/*-- sys.dm_pdw_sql_requests with the correct node id
CREATE VIEW sql_requests AS
(SELECT
       sr.request_id,
       sr.step_index,
       (CASE 
              WHEN (sr.distribution_id = -1 ) THEN 
              (SELECT pdw_node_id FROM sys.dm_pdw_nodes WHERE type = 'CONTROL') 
              ELSE d.pdw_node_id END) AS pdw_node_id,
       sr.distribution_id,
       sr.status,
       sr.error_id,
       sr.start_time,
       sr.end_time,
       sr.total_elapsed_time,
       sr.row_count,
       sr.spid,
       sr.command
FROM sys.pdw_distributions AS d
RIGHT JOIN sys.dm_pdw_sql_requests AS sr ON d.distribution_id = sr.distribution_id)
*/

-- Memory consumption
SELECT
  pc1.pdw_node_id,
  pc1.cntr_value * 100.0/pc2.cntr_value AS Memory_Utilization_Percentage
FROM
-- pc1: current memory
sys.dm_pdw_nodes_os_performance_counters AS pc1
-- pc2: total memory allowed for this SQL instance
JOIN sys.dm_pdw_nodes_os_performance_counters AS pc2 
ON pc1.object_name = pc2.object_name AND pc1.pdw_node_id = pc2.pdw_node_id
WHERE
pc1.counter_name = 'Total Server Memory (KB)'
AND pc2.counter_name = 'Target Server Memory (KB)'


(4 rows affected)

Total execution time: 00:00:01.156

pdw_node_id Memory_Utilization_Percentage 10 1.374289534844639 9 20.953978743175463 19 20.850195846380643 33 20.846388620684424

## Memory Grant

In [7]:
/* Calculating memory grants per table */
SELECT schm_name + '.' + table_name AS Table_name
	--,CAST((table_overhead * 1.0 + column_size + short_string_size + long_string_size) AS DECIMAL(18, 2)) AS est_mem_grant_B
	,CAST((table_overhead * 1.0 + column_size + short_string_size + long_string_size) / 1048576 AS DECIMAL(18, 2)) AS est_mem_grant_MiB
	--,CAST((table_overhead * 1.0 + column_size + short_string_size + long_string_size) / 1073741824 AS DECIMAL(18, 2)) AS est_mem_grant_GiB
FROM (
	SELECT schm_name
		,table_name
		,75497472 AS table_overhead
		,column_count * 1048576 * 8 AS column_size
		,short_string_count * 1048576 * 32 AS short_string_size
		,(long_string_count * 16777216) - (32 * long_string_count) AS long_string_size
	FROM (
		SELECT schm_name
			,table_name
			,SUM(CAST(column_count AS BIGINT)) AS column_count
			,ISNULL(SUM(CAST(short_string_count AS BIGINT)), 0) AS short_string_count
			,ISNULL(SUM(CAST(long_string_count AS BIGINT)), 0) AS long_string_count
		FROM (
			SELECT sm.name AS schm_name
				,tb.name AS table_name
				,COUNT(CAST(co.column_id AS BIGINT)) AS column_count
				,CASE 
					WHEN co.system_type_id IN (
							167
							,175
							,231
							,239
							)
						AND co.max_length <= 32
						THEN COUNT(CAST(co.column_id AS BIGINT))
					END AS short_string_count
				,CASE 
					WHEN co.system_type_id IN (
							167
							,175
							,231
							,239
							)
						AND co.max_length > 32
						THEN COUNT(CAST(co.column_id AS BIGINT))
					END AS long_string_count
			FROM sys.schemas AS sm
			INNER JOIN sys.tables AS tb ON sm.[schema_id] = tb.[schema_id]
			INNER JOIN sys.columns AS co ON tb.[object_id] = co.[object_id]
			GROUP BY sm.name
				,tb.name
				,co.system_type_id
				,co.max_length
			) C
		GROUP BY schm_name
			,table_name
		) B
	) A

order by est_mem_grant_MiB desc 

(318 rows affected)

Total execution time: 00:00:00.325

Table_name est_mem_grant_MiB dbo.v4_Module_Actuals 3248.00 dbo.v4_Module_Model 3248.00 dbo.v3_Module_Model 3208.00 dbo.ctasInputJoinKey 2920.00 dbo.BrockSegmentedPolicyRecords_Final2017Revised 2640.00 dbo.HLRSegmentedPolicyRecords_Final2017Revised 2640.00 dbo.SRUSSegmentedPolicyRecords_Final2017Revised 2640.00 dbo.tmp_databricks_2019_07_25_11_55_56_575_8f3e2cb03c844f80a1c6f2bd4069537f_external_table 2640.00 dbo.tmp_databricks_2019_07_25_12_55_23_606_a0b416c20de7429f87d48b0930807f01_external_table 2640.00 dbo.MMP_sort_4Q18_AllTreaties 2616.00 dbo.ctasSuperTableSum 2368.00 dbo.ctasSuperTableSum20190920 2368.00 dbo.vw_PLT_Use_Case 2256.00 dbo.v3_Module_Model_DropMe2 2104.00 dbo.ctasInputClean 1888.00 dbo.input_12A 1784.00 dbo.v3_Module_Inforce 1776.00 dbo.Input12 1768.00 dbo.v3_Module_Model_DropMe1 1752.00 dbo.ctasCCIDMMPReplicate 1736.00 dbo.ctasPolMMPReplicate 1712.00 dbo.hashOrganicRAMP 1704.00 dbo.Organic_RAMPs_FullStacked 1704.00 dbo.Organic_mmp_4Q18Prod_ONB 1680.00 dbo.Organic_mmp 1640.00 dbo.BrockCAM_mmp_sji 1640.00 dbo.Input11 1632.00 dbo.test_RAMPs_bigmac_srt 1632.00 dbo.test_RAMPs_cwwithret_srt 1632.00 dbo.Test_RAMPsWithCorrectedDates 1608.00 dbo.Test_RAMPsWithCorrectedDates_v3 1608.00 dbo.BrockCAM_mmp_Stacked_DuplicateTape_Rerun 1608.00 dbo.BrockCAM_mmp_Stacked_MaxDateOnly 1608.00 dbo.BrockCAM_mmp_Full_Stacked 1608.00 dbo.BrockCAM_mmp_ked 1608.00 dbo.BrockCAM_mmp_ked_delete2 1608.00 dbo.Test_RAMPsWithCorrectedDates_v2 1592.00 dbo.ctasSuperTableSum0 1576.00 dbo.v3_Module_CashFlows 1464.00 dbo.ctiiSuperTableSum 1408.00 dbo.Model10 1400.00 dbo.Model9 1400.00 dbo.v8_MODULE_MODEL 1400.00 dbo.v7_MODULE_MODEL 1376.00 dbo.v5_MODULE_MODEL 1376.00 dbo.MapCCIDModelFeatures 1336.00 dbo.ctasSuperTable 1336.00 dbo.jp_MAP_CCID_MODEL_FEATURES 1320.00 dbo.v5_MAP_CCID_MODEL_FEATURES 1320.00 dbo.v6_MAP_CCID_MODEL_FEATURES 1288.00 dbo.ctasSuperTableMap 1272.00 dbo.ctiiSuperTableMapMaxMask 1248.00 dbo.Temp_PowerBI_Testing 1240.00 dbo.Temp_PowerBI_Testing_06_24_2019 1240.00 dbo.Temp_PowerBI_Testing_09_06_2019 1240.00 dbo.Temp_PowerBI_Testing_08_06_2019 1224.00 dbo.Inforce11NoHash_TEST 1184.00 dbo.Temp_PowerBI_Testing_05_06_2019 1144.00 dbo.TreatyMap 1144.00 dbo.TreatyMap2 1144.00 dbo.mapTreatyReplicate 1144.00 dbo.SAGEPrem 1056.00 dbo.ctasSuperTableStage 1056.00 dbo.HCF_Organic 1048.00 dbo.HCF_Brock 1032.00 dbo.Rates_IndustryQTables 976.00 dbo.Temp_PowerBI_Testing_Long 888.00 dbo.BlobInbox 872.00 dbo.Inforce12 848.00 dbo.Inforce12xxx 848.00 dbo.Temp_PowerBI_Testing_04_06_2019 824.00 dbo.dev_SuperTable 792.00 dbo.extSeriatimDataWarehouseInforce 768.00 dbo.ctasSeriatimDataWarehouseInforce 768.00 dbo.Temp_PowerBI_Testing_30_05_2019 752.00 dbo.TempDeleteMe3bctas 720.00 dbo.Premium12 712.00 dbo.TempDeleteMe3bctas_1928 688.00 dbo.Inforce12_A 688.00 dbo.ctasSeriatimDataWarehousePremium 680.00 dbo.ctasSuperInforce 672.00 dbo.ctasSuperTableSum1 672.00 dbo.Claim12 648.00 dbo.TempDeleteMe2b 648.00 dbo.ref_TreatyTerms_20180807 648.00 dbo.mapTreatyTermsReplicate 648.00 dbo.TempDeleteMe2bctas 632.00 dbo.TempDeleteMe2bctas_1928 632.00 dbo.TempDeleteMe2b_1928 592.00 dbo.ctasSuperTableActualStage 592.00 dbo.ctasSeriatimDataWarehouseClaim 592.00 dbo.TempDeleteMe2bOne 584.00 dbo.TempDeleteMe4b 584.00 dbo.TempDeleteMe5b 584.00 dbo.BlobInbox2 552.00 dbo.BlobInbox3 552.00 dbo.TempDeleteMe4 528.00 dbo.vwGeneralLedger 528.00 dbo.Output12xxx2 520.00 dbo.Output12 520.00 dbo.ctasBrockStackDupeDrops 520.00 dbo.ctasOutput1 520.00 dbo.Premium9 512.00 dbo.Premium10 512.00 dbo.Premium11 512.00 dbo.Premium11NoHash 512.00 dbo.v8_MODULE_PREMIUM 512.00 dbo.Output12xxx 504.00 dbo.TempDeleteMe3 504.00 dbo.output12_A 504.00 dbo.bestEstimateBrockMarch2010Tape 504.00 dbo.Claim12_A 496.00 dbo.v7_MODULE_PREMIUM 488.00 dbo.v6_MODULE_PREMIUM 488.00 dbo.JAMAS_Data_Brock_v13 480.00 dbo.JAMAS_Data_Brock_v13_NoFilter 480.00 dbo.JAMAS_Data_Brock_v13b 480.00 dbo.JAMAS_Data_Brock_v13b_NoFilter 480.00 dbo.tempDelteMeBrockTest_TEST 480.00 dbo.TempDeleteMe2 472.00 dbo.tempBROCK_MODEL_DATA_AdjRs

## Rowgroup Details

In [8]:
SELECT	sm.[name]                                                       AS [logical_schema_name]
,       tb.[name]                                                       AS [logical_table_name]
,		ps.[distribution_id]                                            AS [distribution_id]
,		ps.[partition_number]
,		ps.[row_group_id]
,		ps.[delta_store_hobt_id]
,		ps.[state_desc]
,		ps.[total_rows]
,		ps.[deleted_rows]
,		ps.[size_in_bytes]
,		ps.[trim_reason_desc]
,		ps.[transition_to_compressed_state_desc]
,		ps.[has_vertipaq_optimization]
,		ps.[created_time]
,		ps.[closed_time]
,		ps.[generation]
FROM    sys.[schemas] sm
JOIN    sys.[tables] tb													ON  sm.[schema_id]          = tb.[schema_id]
JOIN    sys.[pdw_table_mappings] mp										ON  tb.[object_id]          = mp.[object_id]
JOIN    sys.[pdw_nodes_tables] nt										ON  nt.[name]               = mp.[physical_name]
JOIN	sys.[dm_pdw_nodes_db_column_store_row_group_physical_stats]	ps	ON  ps.[object_id]          = nt.[object_id]
																		AND ps.[pdw_node_id]        = nt.[pdw_node_id]
																		AND ps.[distribution_id]    = nt.[distribution_id]

## Rowgroups

In [9]:
SELECT * 
	FROM 
	(SELECT	COUNT(*) AS Memory_Limitation
	FROM    sys.[schemas] sm
	JOIN    sys.[tables] tb													ON  sm.[schema_id]          = tb.[schema_id]
	JOIN    sys.[pdw_table_mappings] mp										ON  tb.[object_id]          = mp.[object_id]
	JOIN    sys.[pdw_nodes_tables] nt										ON  nt.[name]               = mp.[physical_name]
	JOIN	sys.[dm_pdw_nodes_db_column_store_row_group_physical_stats]	ps	ON  ps.[object_id]          = nt.[object_id]
																			AND ps.[pdw_node_id]        = nt.[pdw_node_id]
																			AND ps.[distribution_id]    = nt.[distribution_id]
	WHERE trim_reason_desc = 'MEMORY_LIMITATION') AS A, 
	(SELECT	COUNT(*) AS Bulkload
	FROM    sys.[schemas] sm
	JOIN    sys.[tables] tb													ON  sm.[schema_id]          = tb.[schema_id]
	JOIN    sys.[pdw_table_mappings] mp										ON  tb.[object_id]          = mp.[object_id]
	JOIN    sys.[pdw_nodes_tables] nt										ON  nt.[name]               = mp.[physical_name]
	JOIN	sys.[dm_pdw_nodes_db_column_store_row_group_physical_stats]	ps	ON  ps.[object_id]          = nt.[object_id]
																			AND ps.[pdw_node_id]        = nt.[pdw_node_id]
																			AND ps.[distribution_id]    = nt.[distribution_id]
	WHERE trim_reason_desc = 'BULKLOAD') AS B, 
	(SELECT	COUNT(*) AS Dictionary_Size
	FROM    sys.[schemas] sm
	JOIN    sys.[tables] tb													ON  sm.[schema_id]          = tb.[schema_id]
	JOIN    sys.[pdw_table_mappings] mp										ON  tb.[object_id]          = mp.[object_id]
	JOIN    sys.[pdw_nodes_tables] nt										ON  nt.[name]               = mp.[physical_name]
	JOIN	sys.[dm_pdw_nodes_db_column_store_row_group_physical_stats]	ps	ON  ps.[object_id]          = nt.[object_id]
																			AND ps.[pdw_node_id]        = nt.[pdw_node_id]
																			AND ps.[distribution_id]    = nt.[distribution_id]
	WHERE trim_reason_desc = 'DICTIONARY_SIZE') AS C

(534184 rows affected)

Query was canceled by user

Displaying Top 5000 rows.

Query was canceled by user

Total execution time: 00:00:38.300

logical_schema_name logical_table_name distribution_id partition_number row_group_id delta_store_hobt_id state_desc total_rows deleted_rows size_in_bytes trim_reason_desc transition_to_compressed_state_desc has_vertipaq_optimization created_time closed_time generation dbo Premium9 1 1 7 NULL COMPRESSED 50572 0 1494920 REORG TUPLE_MOVER 1 2019-06-29 05:20:47.357 2019-06-29 05:20:44.880 7 dbo v6_MODULE_PREMIUM 2 1 3 NULL COMPRESSED 854888 0 23563872 BULKLOAD BULKLOAD 1 2019-06-26 11:27:02.757 NULL 4 dbo ctasPolMMPReplicate 3 1 0 72057594230145024 OPEN 5628 0 3317760 NULL NULL NULL 2019-08-28 01:47:55.370 NULL NULL dbo TempDeleteMe 4 1 133 NULL COMPRESSED 270863 0 13409880 BULKLOAD BULKLOAD 1 2019-06-07 18:54:05.320 NULL 133 dbo gaapFactorsv1Replicate 5 1 4 NULL COMPRESSED 152856 0 1368632 BULKLOAD BULKLOAD 1 2019-08-02 16:29:31.770 NULL 5 dbo ctasSeriatimDataWarehouseInforce 6 1 0 NULL COMPRESSED 639062 0 23384656 DICTIONARY_SIZE BULKLOAD 1 2019-09-07 22:29:14.203 NULL 1 dbo JAMAS_Data_Brock_v9 7 1 0 NULL COMPRESSED 199546 0 12442176 BULKLOAD BULKLOAD 1 2019-08-20 21:41:30.060 NULL 1 dbo TempDeleteMe4 8 1 90 72057594118078464 OPEN 304 0 139264 NULL NULL NULL 2019-07-14 06:31:08.930 NULL NULL dbo JAMAS_Data_Brock_v4c 9 1 0 NULL COMPRESSED 220498 0 13719584 BULKLOAD BULKLOAD 1 2019-08-15 17:38:09.910 NULL 1 dbo v7_MODULE_INFORCE 10 1 5 NULL COMPRESSED 328378 0 7848000 DICTIONARY_SIZE BULKLOAD 1 2019-06-26 23:57:09.423 NULL 6 dbo mapPostLevelStatusCtasReplicate 11 1 0 72057594152419328 OPEN 24 0 16384 NULL NULL NULL 2019-07-30 09:00:37.017 NULL NULL dbo mapTreatyReplicate 12 1 0 72057594125811712 OPEN 74 0 65536 NULL NULL NULL 2019-07-15 03:29:38.563 NULL NULL dbo Temp_PowerBI_Testing_06_24_2019 13 1 75 72057594086555648 OPEN 10983 0 8331264 NULL NULL NULL 2019-06-24 22:19:31.070 NULL NULL dbo Brock_4Q18_Prod_Seriatim_Projection 14 1 3 NULL COMPRESSED 250168 0 6733488 BULKLOAD BULKLOAD 1 2019-07-10 12:59:32.007 NULL 4 dbo Premium11 15 1 4 NULL COMPRESSED 104764 0 3342232 DICTIONARY_SIZE BULKLOAD 1 2019-07-09 11:58:28.760 NULL 5 dbo ctasCCIDMMPReplicate 16 1 0 72057594236174336 OPEN 10602 0 6275072 NULL NULL NULL 2019-08-28 01:47:30.447 NULL NULL dbo mapRptOnePostLevelJumpsCtasReplicate 17 1 0 72057594150060032 OPEN 41876 0 1949696 NULL NULL NULL 2019-07-30 09:55:06.930 NULL NULL dbo JAMAS_Data_Brock_v3 18 1 0 NULL COMPRESSED 242777 0 17060304 BULKLOAD BULKLOAD 1 2019-08-07 17:31:35.770 NULL 1 dbo Brock_Stacked_Output_Deleted4 19 1 0 72057594246397952 OPEN 19877 0 5488640 NULL NULL NULL 2019-09-05 21:31:02.330 NULL NULL dbo Brock_4Q18_Prod_Seriatim_Projection 20 1 3 NULL COMPRESSED 250131 0 6749496 BULKLOAD BULKLOAD 1 2019-07-10 12:59:30.670 NULL 4 dbo Output12xxx2 21 1 370 NULL COMPRESSED 292258 0 24380544 BULKLOAD BULKLOAD 1 2019-09-03 02:44:27.743 NULL 371 dbo mapTreatyActualsNoDupeReplicate 22 1 0 72057594128105472 OPEN 60 0 16384 NULL NULL NULL 2019-07-16 10:22:23.580 NULL NULL dbo SAGEPrem 23 1 0 72057594284408832 OPEN 6960 0 2621440 NULL NULL NULL 2019-09-19 21:49:16.200 NULL NULL dbo JAMAS_Data_Brock_v13_Scrubbed 24 1 1 72057594281525248 OPEN 6178 0 1351680 NULL NULL NULL 2019-09-18 19:09:29.053 NULL NULL dbo v5_MODULE_CLAIMS 25 1 2 72057594084196352 OPEN 10518 0 2351104 NULL NULL NULL 2019-06-15 17:42:17.860 NULL NULL dbo JAMAS_Data_Brock_v13_Scrubbed 26 1 1 72057594287554560 OPEN 6141 0 1343488 NULL NULL NULL 2019-09-18 19:09:28.973 NULL NULL dbo ctasDimSystemTreaty 27 1 0 72057594220838912 OPEN 62 0 16384 NULL NULL NULL 2019-08-27 15:06:19.513 NULL NULL dbo Inforce10 28 1 2 NULL COMPRESSED 639904 0 16148504 DICTIONARY_SIZE BULKLOAD 1 2019-07-02 15:53:30.950 NULL 3 dbo ctasMortImprovementCohortJAMAS 29 1 0 72057594272677888 OPEN 12 0 16384 NULL NULL NULL 2019-09-10 04:55:28.133 NULL NULL dbo gaapFactorsReplicate 30 1 4 NULL COMPRESSED 272635 0 2346464 BULKLOAD BULKLOAD 1 2019-08-02 16:34:39.887 NULL 4 dbo v7_MODULE_MODEL 31 1 123 72057594091077632 OPEN 26887 0 10551296 NULL NULL NULL 2019-06-26 22:42:00.813 NULL NULL dbo v

## Skew Detection

In [10]:
/* Returns the data distribution across all distribution databases to help detect any skew */
SELECT 
    distribution_id
,    SUM(reserved_space_GB)        as Data_Size_GB
FROM
(SELECT
   [execution_time]
,  [database_name]
,  [schema_name]
,  [table_name]
,  [two_part_name]
,  [node_table_name]
,  [node_table_name_seq]
,  [distribution_policy_name]
,  [distribution_column]
,  [distribution_id]
,  [index_type]
,  [index_type_desc]
,  [pdw_node_id]
,  [pdw_node_type]
,  [pdw_node_name]
,  [dist_name]
,  [dist_position]
,  [partition_nmbr]
,  [reserved_space_page_count]
,  [unused_space_page_count]
,  [data_space_page_count]
,  [index_space_page_count]
,  [row_count]
,  ([reserved_space_page_count] * 8.0)                                 AS [reserved_space_KB]
,  ([reserved_space_page_count] * 8.0)/1000                            AS [reserved_space_MB]
,  ([reserved_space_page_count] * 8.0)/1000000                         AS [reserved_space_GB]
,  ([reserved_space_page_count] * 8.0)/1000000000                      AS [reserved_space_TB]
,  ([unused_space_page_count]   * 8.0)                                 AS [unused_space_KB]
,  ([unused_space_page_count]   * 8.0)/1000                            AS [unused_space_MB]
,  ([unused_space_page_count]   * 8.0)/1000000                         AS [unused_space_GB]
,  ([unused_space_page_count]   * 8.0)/1000000000                      AS [unused_space_TB]
,  ([data_space_page_count]     * 8.0)                                 AS [data_space_KB]
,  ([data_space_page_count]     * 8.0)/1000                            AS [data_space_MB]
,  ([data_space_page_count]     * 8.0)/1000000                         AS [data_space_GB]
,  ([data_space_page_count]     * 8.0)/1000000000                      AS [data_space_TB]
,  ([index_space_page_count]  * 8.0)                                   AS [index_space_KB]
,  ([index_space_page_count]  * 8.0)/1000                              AS [index_space_MB]
,  ([index_space_page_count]  * 8.0)/1000000                           AS [index_space_GB]
,  ([index_space_page_count]  * 8.0)/1000000000                        AS [index_space_TB]
FROM
	(SELECT 
	 GETDATE()                                                             AS  [execution_time]
	, DB_NAME()                                                            AS  [database_name]
	, s.name                                                               AS  [schema_name]
	, t.name                                                               AS  [table_name]
	, QUOTENAME(s.name)+'.'+QUOTENAME(t.name)                              AS  [two_part_name]
	, nt.[name]                                                            AS  [node_table_name]
	, ROW_NUMBER() OVER(PARTITION BY nt.[name] ORDER BY (SELECT NULL))     AS  [node_table_name_seq]
	, tp.[distribution_policy_desc]                                        AS  [distribution_policy_name]
	, c.[name]                                                             AS  [distribution_column]
	, nt.[distribution_id]                                                 AS  [distribution_id]
	, i.[type]                                                             AS  [index_type]
	, i.[type_desc]                                                        AS  [index_type_desc]
	, nt.[pdw_node_id]                                                     AS  [pdw_node_id]
	, pn.[type]                                                            AS  [pdw_node_type]
	, pn.[name]                                                            AS  [pdw_node_name]
	, di.name                                                              AS  [dist_name]
	, di.position                                                          AS  [dist_position]
	, nps.[partition_number]                                               AS  [partition_nmbr]
	, nps.[reserved_page_count]                                            AS  [reserved_space_page_count]
	, nps.[reserved_page_count] - nps.[used_page_count]                    AS  [unused_space_page_count]
	, nps.[in_row_data_page_count] 
		+ nps.[row_overflow_used_page_count] 
		+ nps.[lob_used_page_count]                                        AS  [data_space_page_count]
	, nps.[reserved_page_count] 
	 - (nps.[reserved_page_count] - nps.[used_page_count]) 
	 - ([in_row_data_page_count] 
			 + [row_overflow_used_page_count]+[lob_used_page_count])       AS  [index_space_page_count]
	, nps.[row_count]                                                      AS  [row_count]
	from 
		sys.schemas s
	INNER JOIN sys.tables t
		ON s.[schema_id] = t.[schema_id]
	INNER JOIN sys.indexes i
		ON  t.[object_id] = i.[object_id]
		AND i.[index_id] <= 1
	INNER JOIN sys.pdw_table_distribution_properties tp
		ON t.[object_id] = tp.[object_id]
	INNER JOIN sys.pdw_table_mappings tm
		ON t.[object_id] = tm.[object_id]
	INNER JOIN sys.pdw_nodes_tables nt
		ON tm.[physical_name] = nt.[name]
	INNER JOIN sys.dm_pdw_nodes pn
		ON  nt.[pdw_node_id] = pn.[pdw_node_id]
	INNER JOIN sys.pdw_distributions di
		ON  nt.[distribution_id] = di.[distribution_id]
	INNER JOIN sys.dm_pdw_nodes_db_partition_stats nps
		ON nt.[object_id] = nps.[object_id]
		AND nt.[pdw_node_id] = nps.[pdw_node_id]
		AND nt.[distribution_id] = nps.[distribution_id]
	LEFT OUTER JOIN (select * from sys.pdw_column_distribution_properties where distribution_ordinal = 1) cdp
		ON t.[object_id] = cdp.[object_id]
	LEFT OUTER JOIN sys.columns c
		ON cdp.[object_id] = c.[object_id]
		AND cdp.[column_id] = c.[column_id]) AS Base) AS Base1
GROUP BY     distribution_id

(60 rows affected)

Total execution time: 00:00:03.350

distribution_id Data_Size_GB 1 254.289776000 2 254.900064000 3 254.900904000 4 254.739392000 5 254.969944000 6 254.553752000 7 254.526232000 8 255.148592000 9 254.517320000 10 254.940528000 11 254.861880000 12 254.771384000 13 254.920792000 14 254.602568000 15 255.173760000 16 254.371376000 17 254.617992000 18 254.182216000 19 254.851872000 20 255.081296000 21 254.266304000 22 254.641416000 23 254.773776000 24 255.135760000 25 255.302848000 26 254.827184000 27 254.644056000 28 254.629328000 29 254.798560000 30 254.334896000 31 254.569024000 32 254.275088000 33 254.174304000 34 254.510584000 35 254.678080000 36 254.671048000 37 254.446448000 38 254.532792000 39 254.818512000 40 254.782376000 41 254.472344000 42 254.148760000 43 254.780032000 44 254.268688000 45 254.611968000 46 254.261304000 47 254.911512000 48 254.572008000 49 255.017888000 50 254.738752000 51 254.939072000 52 254.323216000 53 343.059912000 54 254.575288000 55 254.639736000 56 254.186376000 57 254.438776000 58 254.548584000 59 254.905040000 60 254.700400000

## Slot Usage

In [11]:
-- Total running queries and slots consumed
SELECT
	SUM(CASE WHEN r.[status] ='Running'   THEN 1 ELSE 0 END)							[running_queries]
	, SUM(CASE WHEN r.[status] ='Running'   THEN rw.concurrency_slots_used ELSE 0 END)	[running_queries_slots]
	, SUM(CASE WHEN r.[status] ='Suspended' THEN 1 ELSE 0 END)							[queued_queries]
	, SUM(CASE WHEN rw.[state] ='Queued'    THEN rw.concurrency_slots_used ELSE 0 END)	[queued_queries_slots]
FROM
	[sys].[dm_pdw_exec_requests] r 
	JOIN [sys].[dm_pdw_resource_waits] rw ON rw.request_id = r.request_id
WHERE
	( (r.[status] = 'Running' AND r.[resource_class] IS NOT NULL ) OR r.[status] ='Suspended' )
	AND rw.[type] ='UserConcurrencyResourceType';

(1 row affected)

Total execution time: 00:00:00.235

running_queries running_queries_slots queued_queries queued_queries_slots NULL NULL NULL NULL

## Storage Size

In [12]:
/* Returns reserved space within the database broken down into the data, index, and unused space */
SELECT 'data_space_GB', sum(data_space_GB) AS data_space_GB
    FROM
    (SELECT
    [execution_time]
    ,  [database_name]
    ,  [schema_name]
    ,  [table_name]
    ,  [two_part_name]
    ,  [node_table_name]
    ,  [node_table_name_seq]
    ,  [distribution_policy_name]
    ,  [distribution_column]
    ,  [distribution_id]
    ,  [index_type]
    ,  [index_type_desc]
    ,  [pdw_node_id]
    ,  [pdw_node_type]
    ,  [pdw_node_name]
    ,  [dist_name]
    ,  [dist_position]
    ,  [partition_nmbr]
    ,  [reserved_space_page_count]
    ,  [unused_space_page_count]
    ,  [data_space_page_count]
    ,  [index_space_page_count]
    ,  [row_count]
    ,  ([reserved_space_page_count] * 8.0)                                 AS [reserved_space_KB]
    ,  ([reserved_space_page_count] * 8.0)/1000                            AS [reserved_space_MB]
    ,  ([reserved_space_page_count] * 8.0)/1000000                         AS [reserved_space_GB]
    ,  ([reserved_space_page_count] * 8.0)/1000000000                      AS [reserved_space_TB]
    ,  ([unused_space_page_count]   * 8.0)                                 AS [unused_space_KB]
    ,  ([unused_space_page_count]   * 8.0)/1000                            AS [unused_space_MB]
    ,  ([unused_space_page_count]   * 8.0)/1000000                         AS [unused_space_GB]
    ,  ([unused_space_page_count]   * 8.0)/1000000000                      AS [unused_space_TB]
    ,  ([data_space_page_count]     * 8.0)                                 AS [data_space_KB]
    ,  ([data_space_page_count]     * 8.0)/1000                            AS [data_space_MB]
    ,  ([data_space_page_count]     * 8.0)/1000000                         AS [data_space_GB]
    ,  ([data_space_page_count]     * 8.0)/1000000000                      AS [data_space_TB]
    ,  ([index_space_page_count]  * 8.0)                                   AS [index_space_KB]
    ,  ([index_space_page_count]  * 8.0)/1000                              AS [index_space_MB]
    ,  ([index_space_page_count]  * 8.0)/1000000                           AS [index_space_GB]
    ,  ([index_space_page_count]  * 8.0)/1000000000                        AS [index_space_TB]
    FROM
        (SELECT 
        GETDATE()                                                             AS  [execution_time]
        , DB_NAME()                                                            AS  [database_name]
        , s.name                                                               AS  [schema_name]
        , t.name                                                               AS  [table_name]
        , QUOTENAME(s.name)+'.'+QUOTENAME(t.name)                              AS  [two_part_name]
        , nt.[name]                                                            AS  [node_table_name]
        , ROW_NUMBER() OVER(PARTITION BY nt.[name] ORDER BY (SELECT NULL))     AS  [node_table_name_seq]
        , tp.[distribution_policy_desc]                                        AS  [distribution_policy_name]
        , c.[name]                                                             AS  [distribution_column]
        , nt.[distribution_id]                                                 AS  [distribution_id]
        , i.[type]                                                             AS  [index_type]
        , i.[type_desc]                                                        AS  [index_type_desc]
        , nt.[pdw_node_id]                                                     AS  [pdw_node_id]
        , pn.[type]                                                            AS  [pdw_node_type]
        , pn.[name]                                                            AS  [pdw_node_name]
        , di.name                                                              AS  [dist_name]
        , di.position                                                          AS  [dist_position]
        , nps.[partition_number]                                               AS  [partition_nmbr]
        , nps.[reserved_page_count]                                            AS  [reserved_space_page_count]
        , nps.[reserved_page_count] - nps.[used_page_count]                    AS  [unused_space_page_count]
        , nps.[in_row_data_page_count] 
            + nps.[row_overflow_used_page_count] 
            + nps.[lob_used_page_count]                                        AS  [data_space_page_count]
        , nps.[reserved_page_count] 
        - (nps.[reserved_page_count] - nps.[used_page_count]) 
        - ([in_row_data_page_count] 
                + [row_overflow_used_page_count]+[lob_used_page_count])       AS  [index_space_page_count]
        , nps.[row_count]                                                      AS  [row_count]
        from 
            sys.schemas s
        INNER JOIN sys.tables t
            ON s.[schema_id] = t.[schema_id]
        INNER JOIN sys.indexes i
            ON  t.[object_id] = i.[object_id]
            AND i.[index_id] <= 1
        INNER JOIN sys.pdw_table_distribution_properties tp
            ON t.[object_id] = tp.[object_id]
        INNER JOIN sys.pdw_table_mappings tm
            ON t.[object_id] = tm.[object_id]
        INNER JOIN sys.pdw_nodes_tables nt
            ON tm.[physical_name] = nt.[name]
        INNER JOIN sys.dm_pdw_nodes pn
            ON  nt.[pdw_node_id] = pn.[pdw_node_id]
        INNER JOIN sys.pdw_distributions di
            ON  nt.[distribution_id] = di.[distribution_id]
        INNER JOIN sys.dm_pdw_nodes_db_partition_stats nps
            ON nt.[object_id] = nps.[object_id]
            AND nt.[pdw_node_id] = nps.[pdw_node_id]
            AND nt.[distribution_id] = nps.[distribution_id]
        LEFT OUTER JOIN (select * from sys.pdw_column_distribution_properties where distribution_ordinal = 1) cdp
            ON t.[object_id] = cdp.[object_id]
        LEFT OUTER JOIN sys.columns c
            ON cdp.[object_id] = c.[object_id]
            AND cdp.[column_id] = c.[column_id]) AS Base) AS Base1
UNION ALL
SELECT 'index_space_GB', sum(index_space_GB) AS index_space_GB
    FROM
    (SELECT
    [execution_time]
    ,  [database_name]
    ,  [schema_name]
    ,  [table_name]
    ,  [two_part_name]
    ,  [node_table_name]
    ,  [node_table_name_seq]
    ,  [distribution_policy_name]
    ,  [distribution_column]
    ,  [distribution_id]
    ,  [index_type]
    ,  [index_type_desc]
    ,  [pdw_node_id]
    ,  [pdw_node_type]
    ,  [pdw_node_name]
    ,  [dist_name]
    ,  [dist_position]
    ,  [partition_nmbr]
    ,  [reserved_space_page_count]
    ,  [unused_space_page_count]
    ,  [data_space_page_count]
    ,  [index_space_page_count]
    ,  [row_count]
    ,  ([reserved_space_page_count] * 8.0)                                 AS [reserved_space_KB]
    ,  ([reserved_space_page_count] * 8.0)/1000                            AS [reserved_space_MB]
    ,  ([reserved_space_page_count] * 8.0)/1000000                         AS [reserved_space_GB]
    ,  ([reserved_space_page_count] * 8.0)/1000000000                      AS [reserved_space_TB]
    ,  ([unused_space_page_count]   * 8.0)                                 AS [unused_space_KB]
    ,  ([unused_space_page_count]   * 8.0)/1000                            AS [unused_space_MB]
    ,  ([unused_space_page_count]   * 8.0)/1000000                         AS [unused_space_GB]
    ,  ([unused_space_page_count]   * 8.0)/1000000000                      AS [unused_space_TB]
    ,  ([data_space_page_count]     * 8.0)                                 AS [data_space_KB]
    ,  ([data_space_page_count]     * 8.0)/1000                            AS [data_space_MB]
    ,  ([data_space_page_count]     * 8.0)/1000000                         AS [data_space_GB]
    ,  ([data_space_page_count]     * 8.0)/1000000000                      AS [data_space_TB]
    ,  ([index_space_page_count]  * 8.0)                                   AS [index_space_KB]
    ,  ([index_space_page_count]  * 8.0)/1000                              AS [index_space_MB]
    ,  ([index_space_page_count]  * 8.0)/1000000                           AS [index_space_GB]
    ,  ([index_space_page_count]  * 8.0)/1000000000                        AS [index_space_TB]
    FROM
        (SELECT 
        GETDATE()                                                             AS  [execution_time]
        , DB_NAME()                                                            AS  [database_name]
        , s.name                                                               AS  [schema_name]
        , t.name                                                               AS  [table_name]
        , QUOTENAME(s.name)+'.'+QUOTENAME(t.name)                              AS  [two_part_name]
        , nt.[name]                                                            AS  [node_table_name]
        , ROW_NUMBER() OVER(PARTITION BY nt.[name] ORDER BY (SELECT NULL))     AS  [node_table_name_seq]
        , tp.[distribution_policy_desc]                                        AS  [distribution_policy_name]
        , c.[name]                                                             AS  [distribution_column]
        , nt.[distribution_id]                                                 AS  [distribution_id]
        , i.[type]                                                             AS  [index_type]
        , i.[type_desc]                                                        AS  [index_type_desc]
        , nt.[pdw_node_id]                                                     AS  [pdw_node_id]
        , pn.[type]                                                            AS  [pdw_node_type]
        , pn.[name]                                                            AS  [pdw_node_name]
        , di.name                                                              AS  [dist_name]
        , di.position                                                          AS  [dist_position]
        , nps.[partition_number]                                               AS  [partition_nmbr]
        , nps.[reserved_page_count]                                            AS  [reserved_space_page_count]
        , nps.[reserved_page_count] - nps.[used_page_count]                    AS  [unused_space_page_count]
        , nps.[in_row_data_page_count] 
            + nps.[row_overflow_used_page_count] 
            + nps.[lob_used_page_count]                                        AS  [data_space_page_count]
        , nps.[reserved_page_count] 
        - (nps.[reserved_page_count] - nps.[used_page_count]) 
        - ([in_row_data_page_count] 
                + [row_overflow_used_page_count]+[lob_used_page_count])       AS  [index_space_page_count]
        , nps.[row_count]                                                      AS  [row_count]
        from 
            sys.schemas s
        INNER JOIN sys.tables t
            ON s.[schema_id] = t.[schema_id]
        INNER JOIN sys.indexes i
            ON  t.[object_id] = i.[object_id]
            AND i.[index_id] <= 1
        INNER JOIN sys.pdw_table_distribution_properties tp
            ON t.[object_id] = tp.[object_id]
        INNER JOIN sys.pdw_table_mappings tm
            ON t.[object_id] = tm.[object_id]
        INNER JOIN sys.pdw_nodes_tables nt
            ON tm.[physical_name] = nt.[name]
        INNER JOIN sys.dm_pdw_nodes pn
            ON  nt.[pdw_node_id] = pn.[pdw_node_id]
        INNER JOIN sys.pdw_distributions di
            ON  nt.[distribution_id] = di.[distribution_id]
        INNER JOIN sys.dm_pdw_nodes_db_partition_stats nps
            ON nt.[object_id] = nps.[object_id]
            AND nt.[pdw_node_id] = nps.[pdw_node_id]
            AND nt.[distribution_id] = nps.[distribution_id]
        LEFT OUTER JOIN (select * from sys.pdw_column_distribution_properties where distribution_ordinal = 1) cdp
            ON t.[object_id] = cdp.[object_id]
        LEFT OUTER JOIN sys.columns c
            ON cdp.[object_id] = c.[object_id]
            AND cdp.[column_id] = c.[column_id]) AS Base) AS Base1
UNION ALL
SELECT 'unused_space_GB', sum(unused_space_GB) AS unused_space_GB
    FROM
    (SELECT
    [execution_time]
    ,  [database_name]
    ,  [schema_name]
    ,  [table_name]
    ,  [two_part_name]
    ,  [node_table_name]
    ,  [node_table_name_seq]
    ,  [distribution_policy_name]
    ,  [distribution_column]
    ,  [distribution_id]
    ,  [index_type]
    ,  [index_type_desc]
    ,  [pdw_node_id]
    ,  [pdw_node_type]
    ,  [pdw_node_name]
    ,  [dist_name]
    ,  [dist_position]
    ,  [partition_nmbr]
    ,  [reserved_space_page_count]
    ,  [unused_space_page_count]
    ,  [data_space_page_count]
    ,  [index_space_page_count]
    ,  [row_count]
    ,  ([reserved_space_page_count] * 8.0)                                 AS [reserved_space_KB]
    ,  ([reserved_space_page_count] * 8.0)/1000                            AS [reserved_space_MB]
    ,  ([reserved_space_page_count] * 8.0)/1000000                         AS [reserved_space_GB]
    ,  ([reserved_space_page_count] * 8.0)/1000000000                      AS [reserved_space_TB]
    ,  ([unused_space_page_count]   * 8.0)                                 AS [unused_space_KB]
    ,  ([unused_space_page_count]   * 8.0)/1000                            AS [unused_space_MB]
    ,  ([unused_space_page_count]   * 8.0)/1000000                         AS [unused_space_GB]
    ,  ([unused_space_page_count]   * 8.0)/1000000000                      AS [unused_space_TB]
    ,  ([data_space_page_count]     * 8.0)                                 AS [data_space_KB]
    ,  ([data_space_page_count]     * 8.0)/1000                            AS [data_space_MB]
    ,  ([data_space_page_count]     * 8.0)/1000000                         AS [data_space_GB]
    ,  ([data_space_page_count]     * 8.0)/1000000000                      AS [data_space_TB]
    ,  ([index_space_page_count]  * 8.0)                                   AS [index_space_KB]
    ,  ([index_space_page_count]  * 8.0)/1000                              AS [index_space_MB]
    ,  ([index_space_page_count]  * 8.0)/1000000                           AS [index_space_GB]
    ,  ([index_space_page_count]  * 8.0)/1000000000                        AS [index_space_TB]
    FROM
        (SELECT 
        GETDATE()                                                             AS  [execution_time]
        , DB_NAME()                                                            AS  [database_name]
        , s.name                                                               AS  [schema_name]
        , t.name                                                               AS  [table_name]
        , QUOTENAME(s.name)+'.'+QUOTENAME(t.name)                              AS  [two_part_name]
        , nt.[name]                                                            AS  [node_table_name]
        , ROW_NUMBER() OVER(PARTITION BY nt.[name] ORDER BY (SELECT NULL))     AS  [node_table_name_seq]
        , tp.[distribution_policy_desc]                                        AS  [distribution_policy_name]
        , c.[name]                                                             AS  [distribution_column]
        , nt.[distribution_id]                                                 AS  [distribution_id]
        , i.[type]                                                             AS  [index_type]
        , i.[type_desc]                                                        AS  [index_type_desc]
        , nt.[pdw_node_id]                                                     AS  [pdw_node_id]
        , pn.[type]                                                            AS  [pdw_node_type]
        , pn.[name]                                                            AS  [pdw_node_name]
        , di.name                                                              AS  [dist_name]
        , di.position                                                          AS  [dist_position]
        , nps.[partition_number]                                               AS  [partition_nmbr]
        , nps.[reserved_page_count]                                            AS  [reserved_space_page_count]
        , nps.[reserved_page_count] - nps.[used_page_count]                    AS  [unused_space_page_count]
        , nps.[in_row_data_page_count] 
            + nps.[row_overflow_used_page_count] 
            + nps.[lob_used_page_count]                                        AS  [data_space_page_count]
        , nps.[reserved_page_count] 
        - (nps.[reserved_page_count] - nps.[used_page_count]) 
        - ([in_row_data_page_count] 
                + [row_overflow_used_page_count]+[lob_used_page_count])       AS  [index_space_page_count]
        , nps.[row_count]                                                      AS  [row_count]
        from 
            sys.schemas s
        INNER JOIN sys.tables t
            ON s.[schema_id] = t.[schema_id]
        INNER JOIN sys.indexes i
            ON  t.[object_id] = i.[object_id]
            AND i.[index_id] <= 1
        INNER JOIN sys.pdw_table_distribution_properties tp
            ON t.[object_id] = tp.[object_id]
        INNER JOIN sys.pdw_table_mappings tm
            ON t.[object_id] = tm.[object_id]
        INNER JOIN sys.pdw_nodes_tables nt
            ON tm.[physical_name] = nt.[name]
        INNER JOIN sys.dm_pdw_nodes pn
            ON  nt.[pdw_node_id] = pn.[pdw_node_id]
        INNER JOIN sys.pdw_distributions di
            ON  nt.[distribution_id] = di.[distribution_id]
        INNER JOIN sys.dm_pdw_nodes_db_partition_stats nps
            ON nt.[object_id] = nps.[object_id]
            AND nt.[pdw_node_id] = nps.[pdw_node_id]
            AND nt.[distribution_id] = nps.[distribution_id]
        LEFT OUTER JOIN (select * from sys.pdw_column_distribution_properties where distribution_ordinal = 1) cdp
            ON t.[object_id] = cdp.[object_id]
        LEFT OUTER JOIN sys.columns c
            ON cdp.[object_id] = c.[object_id]
            AND cdp.[column_id] = c.[column_id]) AS Base) AS Base1

(3 rows affected)

Total execution time: 00:00:08.824

(No column name) data_space_GB data_space_GB 15362.627568000 index_space_GB 3.070120000 unused_space_GB 2.135992000

## Table Health Count

In [13]:
/* Retuns the number of tables which may be suffering from poor quality segments */

Select * FROM 
(
    SELECT    Count(*) AS Poor_Quality_Segments
    FROM
        (SELECT
        GETDATE()                                                               AS [execution_date]
,       DB_Name()                                                               AS [database_name]
,       s.name                                                                  AS [schema_name]
,       t.name                                                                  AS [table_name]
,    COUNT(DISTINCT rg.[partition_number])                    AS [table_partition_count]
,       SUM(rg.[total_rows])                                                    AS [row_count_total]
,       SUM(rg.[total_rows])/COUNT(DISTINCT rg.[distribution_id])               AS [row_count_per_distribution_MAX]
,    CEILING    ((SUM(rg.[total_rows])*1.0/COUNT(DISTINCT rg.[distribution_id]))/1048576) AS [rowgroup_per_distribution_MAX]
,       SUM(CASE WHEN rg.[State] = 0 THEN 1                   ELSE 0    END)    AS [INVISIBLE_rowgroup_count]
,       SUM(CASE WHEN rg.[State] = 0 THEN rg.[total_rows]     ELSE 0    END)    AS [INVISIBLE_rowgroup_rows]
,       MIN(CASE WHEN rg.[State] = 0 THEN rg.[total_rows]     ELSE NULL END)    AS [INVISIBLE_rowgroup_rows_MIN]
,       MAX(CASE WHEN rg.[State] = 0 THEN rg.[total_rows]     ELSE NULL END)    AS [INVISIBLE_rowgroup_rows_MAX]
,       AVG(CASE WHEN rg.[State] = 0 THEN rg.[total_rows]     ELSE NULL END)    AS [INVISIBLE_rowgroup_rows_AVG]
,       SUM(CASE WHEN rg.[State] = 1 THEN 1                   ELSE 0    END)    AS [OPEN_rowgroup_count]
,       SUM(CASE WHEN rg.[State] = 1 THEN rg.[total_rows]     ELSE 0    END)    AS [OPEN_rowgroup_rows]
,       MIN(CASE WHEN rg.[State] = 1 THEN rg.[total_rows]     ELSE NULL END)    AS [OPEN_rowgroup_rows_MIN]
,       MAX(CASE WHEN rg.[State] = 1 THEN rg.[total_rows]     ELSE NULL END)    AS [OPEN_rowgroup_rows_MAX]
,       AVG(CASE WHEN rg.[State] = 1 THEN rg.[total_rows]     ELSE NULL END)    AS [OPEN_rowgroup_rows_AVG]
,       SUM(CASE WHEN rg.[State] = 2 THEN 1                   ELSE 0    END)    AS [CLOSED_rowgroup_count]
,       SUM(CASE WHEN rg.[State] = 2 THEN rg.[total_rows]     ELSE 0    END)    AS [CLOSED_rowgroup_rows]
,       MIN(CASE WHEN rg.[State] = 2 THEN rg.[total_rows]     ELSE NULL END)    AS [CLOSED_rowgroup_rows_MIN]
,       MAX(CASE WHEN rg.[State] = 2 THEN rg.[total_rows]     ELSE NULL END)    AS [CLOSED_rowgroup_rows_MAX]
,       AVG(CASE WHEN rg.[State] = 2 THEN rg.[total_rows]     ELSE NULL END)    AS [CLOSED_rowgroup_rows_AVG]
,       SUM(CASE WHEN rg.[State] = 3 THEN 1                   ELSE 0    END)    AS [COMPRESSED_rowgroup_count]
,       SUM(CASE WHEN rg.[State] = 3 THEN rg.[total_rows]     ELSE 0    END)    AS [COMPRESSED_rowgroup_rows]
,       SUM(CASE WHEN rg.[State] = 3 THEN rg.[deleted_rows]   ELSE 0    END)    AS [COMPRESSED_rowgroup_rows_DELETED]
,       MIN(CASE WHEN rg.[State] = 3 THEN rg.[total_rows]     ELSE NULL END)    AS [COMPRESSED_rowgroup_rows_MIN]
,       MAX(CASE WHEN rg.[State] = 3 THEN rg.[total_rows]     ELSE NULL END)    AS [COMPRESSED_rowgroup_rows_MAX]
,       AVG(CASE WHEN rg.[State] = 3 THEN rg.[total_rows]     ELSE NULL END)    AS [COMPRESSED_rowgroup_rows_AVG]
,       'ALTER INDEX ALL ON ' + s.name + '.' + t.NAME + ' REBUILD;'             AS [Rebuild_Index_SQL]
FROM    sys.[pdw_nodes_column_store_row_groups] rg
JOIN    sys.[pdw_nodes_tables] nt                   ON  rg.[object_id]          = nt.[object_id]
                                                    AND rg.[pdw_node_id]        = nt.[pdw_node_id]
                                                    AND rg.[distribution_id]    = nt.[distribution_id]
JOIN    sys.[pdw_table_mappings] mp                 ON  nt.[name]               = mp.[physical_name]
JOIN    sys.[tables] t                              ON  mp.[object_id]          = t.[object_id]
JOIN    sys.[schemas] s                             ON t.[schema_id]            = s.[schema_id]
GROUP BY
        s.[name]
,       t.[name]) AS segmentQuality
    WHERE    COMPRESSED_rowgroup_rows_AVG < 100000
            OR INVISIBLE_rowgroup_rows_AVG < 100000
) A, 
(
SELECT
    COUNT(*) AS Stale_Stats_7_Days
FROM
    sys.objects ob
    JOIN sys.stats st
        ON  ob.[object_id] = st.[object_id]
    JOIN sys.stats_columns sc    
        ON  st.[stats_id] = sc.[stats_id]
        AND st.[object_id] = sc.[object_id]
    JOIN sys.columns co    
        ON  sc.[column_id] = co.[column_id]
        AND sc.[object_id] = co.[object_id]
    JOIN sys.types  ty    
        ON  co.[user_type_id] = ty.[user_type_id]
    JOIN sys.tables tb    
        ON  co.[object_id] = tb.[object_id]
    JOIN sys.schemas sm    
        ON  tb.[schema_id] = sm.[schema_id]
WHERE
    st.[user_created] = 1
AND STATS_DATE(st.[object_id],st.[stats_id]) < dateadd(day,-7,getdate())) B

(1 row affected)

Total execution time: 00:00:03.370

Poor_Quality_Segments Stale_Stats_7_Days 17 0

## Tempdb Consumption

In [14]:
/* Monitor tempdb per compute node */
SELECT
    ssu.pdw_node_id,
    (SUM((ssu.user_objects_alloc_page_count * 8)) + SUM((ssu.internal_objects_alloc_page_count * 8))) AS 'Tempdb_Space_Allocated_KB'
FROM sys.dm_pdw_nodes_db_session_space_usage AS ssu
WHERE DB_NAME(ssu.database_id) = 'tempdb'
GROUP BY ssu.pdw_node_id

(4 rows affected)

Total execution time: 00:00:00.359

pdw_node_id Tempdb_Space_Allocated_KB 9 128 10 91008 19 128 33 128

## User Activites

In [15]:
/* Monitor active sessions, queries, and queried queries */
SELECT * FROM
(
    -- Active Sessions
    SELECT COUNT(*) AS Active_Sessions
    FROM sys.dm_pdw_exec_sessions 
    WHERE status <> 'Closed' and session_id <> session_id()
) A, 
(
    -- Active Queries
    SELECT COUNT(*) AS Active_Queries
    FROM sys.dm_pdw_exec_requests 
    WHERE status not in ('Completed','Failed','Cancelled')
    AND session_id <> session_id()
) B,
(-- Waiting Queued queries
    SELECT COUNT(*) AS Queued_Queries
    FROM   sys.dm_pdw_waits waits
    JOIN  sys.dm_pdw_exec_requests requests
    ON waits.request_id=requests.request_id
    WHERE status <> 'Closed' and waits.session_id <> session_id() and waits.state = 'AcquireResources'
) C,
(-- Waiting load queries
    SELECT Count(*) AS Loads
    FROM
       sys.dm_pdw_dms_external_work s INNER JOIN 
    sys.dm_pdw_exec_requests r
        ON r.request_id = s.request_id
    --WHERE command IN('%CREATE TABLE AS%', '%INSERT%') AND r.status = 'Running' 
) D

(1 row affected)

Total execution time: 00:00:00.494

Active_Sessions Active_Queries Queued_Queries Loads 9 0 0 0

## User Activities Details

In [16]:
SELECT *
FROM sys.dm_pdw_exec_sessions 
WHERE status <> 'Closed' 
and session_id <> session_id()

(9 rows affected)

Total execution time: 00:00:00.151

session_id status request_id security_id login_name login_time query_count is_transactional client_id app_name sql_spid SID171655 Idle NULL NULL System 2019-10-01 12:19:15.193 229 0 System Internal 201 SID171743 Idle NULL NULL LoaderXL 2019-10-01 14:24:35.017 14 0 4.14.90.229:16256 azdata-languageService 204 SID171717 Idle NULL NULL LoaderXL 2019-10-01 14:12:50.603 183 0 4.14.90.229:2496 azdata-languageService 755 SID171747 Idle NULL NULL LoaderXL 2019-10-01 14:24:38.580 14 0 4.14.90.229:5936 azdata-languageService 766 SID171742 Idle NULL NULL LoaderXL 2019-10-01 14:24:34.127 14 0 4.14.90.229:63232 azdata-languageService 143 SID171745 Idle NULL NULL LoaderXL 2019-10-01 14:24:36.830 14 0 4.14.90.229:59776 azdata-languageService 246 SID171736 Idle NULL NULL LoaderXL 2019-10-01 14:20:48.363 14 0 4.14.90.229:32632 azdata-languageService 151 SID171746 Idle NULL NULL LoaderXL 2019-10-01 14:24:37.733 14 0 4.14.90.229:54144 azdata-languageService 754 SID171744 Idle NULL NULL LoaderXL 2019-10-01 14:24:35.937 14 0 4.14.90.229:30584 azdata-languageService 208